# Evaluate building completeness

In support of an ongoing project in Nigeria, we are investigating and evaluating the results of a building digitization effort. The following analyses will be performed to assess the completeness of the digitization effort.

1. Attribute evaluation  
   a. ensure variables in verification protocol are present  
   b. ensure relationship between parcel owner and building occupants  
2. Coverage evaluation  
   a. Calculate across the area in a consistently sized grid (250m)  
   b. Compare building density to Google Buildings  

In [1]:
import sys, os, importlib
import folium

import pandas as pd
import geopandas as gpd
import GOSTRocks.rasterMisc as rMisc
import GOSTRocks.misc as misc

from shapely.geometry import Point, box
from shapely.wkt import loads

from math import ceil
import numpy as np
from shapely.geometry import Polygon

In [77]:
in_folder = "/home/public/Data/COUNTRY/NGA"
out_folder = "/home/wb411133/projects/NGA_buildings/Delta/Results"
if not os.path.exists(out_folder):
    os.makedirs(out_folder)
in_buildings_file = os.path.join(in_folder, "Building.shp")
in_parcels_file = os.path.join(in_folder, "Parcel.shp")
da_buildings = "/home/wb411133/projects/NGA_buildings/MAXAR_DA_Buildings.shp"

# Define paramters
crs = 3857
m_crs = f'epsg:{crs}' # projection used to calculate metre measurements
res = 250 # resolution of 

# Define outputs
summary_grid = f'/home/wb411133/projects/NGA_buildings/Delta/NGA_summary_grid_{res}.shp'
google_buildings_csv = os.path.join(out_folder, "google_buildings.csv")

In [4]:
inB = gpd.read_file(in_buildings_file)
inB = inB.to_crs(m_crs)
inP = gpd.read_file(in_parcels_file)
inP = inP.to_crs(m_crs)

b_idx = inB.sindex
p_idx = inP.sindex

# Calculate general statistics

In [ ]:
print(f'Total number of buildings: {inB.shape[0]}')
print(f'Total area of buildings: {inB["BLD_SIZE_M"].sum()}')
      
print(f'Total number of parcels: {inP.shape[0]}')
print(f'Total area of parcels: {inP["PARCEL_SIZ"].sum()}')

# Find, downlaod, and process Google Buildings

In [ ]:
# read in the google buildings extents file to determine file to download
google_extents = gpd.read_file('/home/public/Data/GLOBAL/Buildings/google_tiles.geojson')
sel_extents = google_extents.loc[google_extents.intersects(inB.unary_union)]

In [13]:
os.path.exists(google_buildings_csv)

True

In [14]:
if not os.path.exists(google_buildings_csv):
    # may need to download buildings
    google_buildings = '/home/public/Data/GLOBAL/Buildings/105_buildings.csv'
    inG = pd.read_csv(google_buildings)
    b = inB.total_bounds
    selG = inG.loc[(inG['longitude'] > b[0]) & (inG['longitude'] < b[2]) & (inG['latitude'] > b[1]) & (inG['latitude'] < b[3])]
    selG.to_csv(google_buildings_csv)
else:
    selG = pd.read_csv(google_buildings_csv)


In [15]:
inG_geom = selG['geometry'].apply(loads)
inG = gpd.GeoDataFrame(selG, geometry=inG_geom, crs='epsg:4326')
inG = inG.to_crs(m_crs)

In [16]:
g_idx = inG.sindex

# Assess attribute completeness
1. Size of the parcel (based on polygon)
2. **Number of structures in parcel, number of occupancy units**  
   a. This is not found in the parcel datasets, but can be calculated.
3. The use of each structure and unit
4. The name, ID, and contact details for the owner of the parcel, and the owner or occupier of the structure, or unit


In [17]:
# Calculate null values in buildings dataset
for col in inB.columns:
    cur_col = inB.loc[:,col]
    print(f'{col}: {cur_col.isna().sum()}')

OWNER_OCCU: 0
WARD: 0
LGA: 0
STATE: 0
BLD_HGT_MT: 0
BLD_USE: 0
WALL_MATRL: 0
ROOF_MATRL: 0
GRID_CONCT: 0
CITY_TOWN: 0
STR_NAME: 14346
BLD_SIZE_M: 0
CENTROIDX: 0
CENTROIDY: 0
geometry: 0


In [ ]:
# Get count of null valus in STR_NAME grouped by BLD_USE
inB.loc[inB['STR_NAME'].isna()]['BLD_USE'].value_counts()

# Summarize buildings within a grid

Create a 250m grid across the study arera and summarize bulidngs and parcels within

In [63]:
# Open DA buildings
inDA = gpd.read_file(da_buildings)
inDA = inDA.to_crs(m_crs)
da_idx = inDA.sindex

In [ ]:
tempP = inP.to_crs(m_crs)
allP = tempP.unary_union

In [78]:
# Generate the grid
if not os.path.exists(summary_grid):
    cols = list(np.arange(xmin, xmax + gridWidth, gridWidth))
    rows = list(np.arange(ymin, ymax + gridHeight, gridHeight))
    all_res = []
    for x in cols:
        for y in rows:
            poly = Polygon([(x,y), (x+gridWidth, y), (x+gridWidth, y+gridHeight), (x, y+gridHeight)])
            if poly.intersects(allP):
                all_res.append([x,y,poly])        
    grid = gpd.GeoDataFrame(pd.DataFrame(all_res, columns=['rowIdx', 'colIdx', 'geometry']), geometry='geometry', crs=f'epsg:{crsNum}')
    grid.to_file(summary_grid)
else:
    grid = gpd.read_file(summary_grid)

In [79]:
if grid.crs != inB.crs:
    grid = grid.to_crs(inB.crs)

In [91]:
grid['per_b'] = 0.
grid['per_p'] = 0.
grid['per_g'] = 0.
grid['per_da']= 0.
for idx, row in grid.iterrows():
    # identify intersecting da buildings 
    potential_da = inDA.loc[list(da_idx.intersection(row['geometry'].bounds))]    
    i_da = potential_da.loc[potential_da.intersects(row['geometry'])]
    c_da = potential_da.loc[potential_da['geometry'].apply(lambda x: row['geometry'].contains(x))]
        
    # identify intersecting google buildings 
    potential_google = inG.loc[list(g_idx.intersection(row['geometry'].bounds))]    
    i_g = potential_google.loc[potential_google.intersects(row['geometry'])]
    c_g = potential_google.loc[potential_google['geometry'].apply(lambda x: row['geometry'].contains(x))]
        
    # identify intersecting buildings 
    potential_buildings = inB.loc[list(b_idx.intersection(row['geometry'].bounds))]    
    i_bld = potential_buildings.loc[potential_buildings.intersects(row['geometry'])]
    c_bld = potential_buildings.loc[potential_buildings['geometry'].apply(lambda x: row['geometry'].contains(x))]
    
    # identify intersecting parcels
    potential_parcels = inP.loc[list(p_idx.intersection(row['geometry'].bounds))]    
    i_par = potential_parcels.loc[potential_parcels.intersects(row['geometry'])]
    c_par = potential_parcels.loc[potential_parcels['geometry'].apply(lambda x: row['geometry'].contains(x))]
    
    # calulate percent parcel and percent built
    try:
        per_da = row['geometry'].intersection(i_da.unary_union).area/row['geometry'].area
    except:
        per_da = 0
    try:
        per_google = row['geometry'].intersection(i_g.unary_union).area/row['geometry'].area
    except:
        per_google = 0
    try:
        per_building = row['geometry'].intersection(i_bld.unary_union).area/row['geometry'].area
    except:
        per_building = 0
    try:
        per_parcel   = row['geometry'].intersection(i_par.unary_union).area/row['geometry'].area
    except:
        per_parcel = 0
        
    grid.loc[idx, 'per_b'] = per_building
    grid.loc[idx, 'per_p'] = per_parcel
    grid.loc[idx, 'per_g'] = per_google
    grid.loc[idx, 'per_da']= per_da

    '''# uncomment this section to stop the loop add a specific index in order to run plotting below
    if idx > 3:
        break'''
    

/home/wb411133/.conda/envs/geog/lib/python3.9/site-packages/shapely/topology.py:19: ShapelyDeprecationWarning: InvalidGeometryError will derive from ShapelyError and not TypeError or ValueError in Shapely 2.0.
  raise InvalidGeometryError("Null geometry supports no operations")
/home/wb411133/.conda/envs/geog/lib/python3.9/site-packages/shapely/topology.py:19: ShapelyDeprecationWarning: InvalidGeometryError will derive from ShapelyError and not TypeError or ValueError in Shapely 2.0.
  raise InvalidGeometryError("Null geometry supports no operations")
/home/wb411133/.conda/envs/geog/lib/python3.9/site-packages/shapely/topology.py:19: ShapelyDeprecationWarning: InvalidGeometryError will derive from ShapelyError and not TypeError or ValueError in Shapely 2.0.
  raise InvalidGeometryError("Null geometry supports no operations")
/home/wb411133/.conda/envs/geog/lib/python3.9/site-packages/shapely/topology.py:19: ShapelyDeprecationWarning: InvalidGeometryError will derive from ShapelyError a

/home/wb411133/.conda/envs/geog/lib/python3.9/site-packages/shapely/topology.py:19: ShapelyDeprecationWarning: InvalidGeometryError will derive from ShapelyError and not TypeError or ValueError in Shapely 2.0.
  raise InvalidGeometryError("Null geometry supports no operations")
/home/wb411133/.conda/envs/geog/lib/python3.9/site-packages/shapely/topology.py:19: ShapelyDeprecationWarning: InvalidGeometryError will derive from ShapelyError and not TypeError or ValueError in Shapely 2.0.
  raise InvalidGeometryError("Null geometry supports no operations")
/home/wb411133/.conda/envs/geog/lib/python3.9/site-packages/shapely/topology.py:19: ShapelyDeprecationWarning: InvalidGeometryError will derive from ShapelyError and not TypeError or ValueError in Shapely 2.0.
  raise InvalidGeometryError("Null geometry supports no operations")
/home/wb411133/.conda/envs/geog/lib/python3.9/site-packages/shapely/topology.py:19: ShapelyDeprecationWarning: InvalidGeometryError will derive from ShapelyError a

/home/wb411133/.conda/envs/geog/lib/python3.9/site-packages/shapely/topology.py:19: ShapelyDeprecationWarning: InvalidGeometryError will derive from ShapelyError and not TypeError or ValueError in Shapely 2.0.
  raise InvalidGeometryError("Null geometry supports no operations")
/home/wb411133/.conda/envs/geog/lib/python3.9/site-packages/shapely/topology.py:19: ShapelyDeprecationWarning: InvalidGeometryError will derive from ShapelyError and not TypeError or ValueError in Shapely 2.0.
  raise InvalidGeometryError("Null geometry supports no operations")
/home/wb411133/.conda/envs/geog/lib/python3.9/site-packages/shapely/topology.py:19: ShapelyDeprecationWarning: InvalidGeometryError will derive from ShapelyError and not TypeError or ValueError in Shapely 2.0.
  raise InvalidGeometryError("Null geometry supports no operations")
/home/wb411133/.conda/envs/geog/lib/python3.9/site-packages/shapely/topology.py:19: ShapelyDeprecationWarning: InvalidGeometryError will derive from ShapelyError a

/home/wb411133/.conda/envs/geog/lib/python3.9/site-packages/shapely/topology.py:19: ShapelyDeprecationWarning: InvalidGeometryError will derive from ShapelyError and not TypeError or ValueError in Shapely 2.0.
  raise InvalidGeometryError("Null geometry supports no operations")
/home/wb411133/.conda/envs/geog/lib/python3.9/site-packages/shapely/topology.py:19: ShapelyDeprecationWarning: InvalidGeometryError will derive from ShapelyError and not TypeError or ValueError in Shapely 2.0.
  raise InvalidGeometryError("Null geometry supports no operations")
/home/wb411133/.conda/envs/geog/lib/python3.9/site-packages/shapely/topology.py:19: ShapelyDeprecationWarning: InvalidGeometryError will derive from ShapelyError and not TypeError or ValueError in Shapely 2.0.
  raise InvalidGeometryError("Null geometry supports no operations")
/home/wb411133/.conda/envs/geog/lib/python3.9/site-packages/shapely/topology.py:19: ShapelyDeprecationWarning: InvalidGeometryError will derive from ShapelyError a

/home/wb411133/.conda/envs/geog/lib/python3.9/site-packages/shapely/topology.py:19: ShapelyDeprecationWarning: InvalidGeometryError will derive from ShapelyError and not TypeError or ValueError in Shapely 2.0.
  raise InvalidGeometryError("Null geometry supports no operations")
/home/wb411133/.conda/envs/geog/lib/python3.9/site-packages/shapely/topology.py:19: ShapelyDeprecationWarning: InvalidGeometryError will derive from ShapelyError and not TypeError or ValueError in Shapely 2.0.
  raise InvalidGeometryError("Null geometry supports no operations")
/home/wb411133/.conda/envs/geog/lib/python3.9/site-packages/shapely/topology.py:19: ShapelyDeprecationWarning: InvalidGeometryError will derive from ShapelyError and not TypeError or ValueError in Shapely 2.0.
  raise InvalidGeometryError("Null geometry supports no operations")
/home/wb411133/.conda/envs/geog/lib/python3.9/site-packages/shapely/topology.py:19: ShapelyDeprecationWarning: InvalidGeometryError will derive from ShapelyError a

...

/home/wb411133/.conda/envs/geog/lib/python3.9/site-packages/shapely/topology.py:19: ShapelyDeprecationWarning: InvalidGeometryError will derive from ShapelyError and not TypeError or ValueError in Shapely 2.0.
  raise InvalidGeometryError("Null geometry supports no operations")
/home/wb411133/.conda/envs/geog/lib/python3.9/site-packages/shapely/topology.py:19: ShapelyDeprecationWarning: InvalidGeometryError will derive from ShapelyError and not TypeError or ValueError in Shapely 2.0.
  raise InvalidGeometryError("Null geometry supports no operations")
/home/wb411133/.conda/envs/geog/lib/python3.9/site-packages/shapely/topology.py:19: ShapelyDeprecationWarning: InvalidGeometryError will derive from ShapelyError and not TypeError or ValueError in Shapely 2.0.
  raise InvalidGeometryError("Null geometry supports no operations")
/home/wb411133/.conda/envs/geog/lib/python3.9/site-packages/shapely/topology.py:19: ShapelyDeprecationWarning: InvalidGeometryError will derive from ShapelyError a

/home/wb411133/.conda/envs/geog/lib/python3.9/site-packages/shapely/topology.py:19: ShapelyDeprecationWarning: InvalidGeometryError will derive from ShapelyError and not TypeError or ValueError in Shapely 2.0.
  raise InvalidGeometryError("Null geometry supports no operations")
/home/wb411133/.conda/envs/geog/lib/python3.9/site-packages/shapely/topology.py:19: ShapelyDeprecationWarning: InvalidGeometryError will derive from ShapelyError and not TypeError or ValueError in Shapely 2.0.
  raise InvalidGeometryError("Null geometry supports no operations")
/home/wb411133/.conda/envs/geog/lib/python3.9/site-packages/shapely/topology.py:19: ShapelyDeprecationWarning: InvalidGeometryError will derive from ShapelyError and not TypeError or ValueError in Shapely 2.0.
  raise InvalidGeometryError("Null geometry supports no operations")
/home/wb411133/.conda/envs/geog/lib/python3.9/site-packages/shapely/topology.py:19: ShapelyDeprecationWarning: InvalidGeometryError will derive from ShapelyError a

/home/wb411133/.conda/envs/geog/lib/python3.9/site-packages/shapely/topology.py:19: ShapelyDeprecationWarning: InvalidGeometryError will derive from ShapelyError and not TypeError or ValueError in Shapely 2.0.
  raise InvalidGeometryError("Null geometry supports no operations")
/home/wb411133/.conda/envs/geog/lib/python3.9/site-packages/shapely/topology.py:19: ShapelyDeprecationWarning: InvalidGeometryError will derive from ShapelyError and not TypeError or ValueError in Shapely 2.0.
  raise InvalidGeometryError("Null geometry supports no operations")
/home/wb411133/.conda/envs/geog/lib/python3.9/site-packages/shapely/topology.py:19: ShapelyDeprecationWarning: InvalidGeometryError will derive from ShapelyError and not TypeError or ValueError in Shapely 2.0.
  raise InvalidGeometryError("Null geometry supports no operations")
/home/wb411133/.conda/envs/geog/lib/python3.9/site-packages/shapely/topology.py:19: ShapelyDeprecationWarning: InvalidGeometryError will derive from ShapelyError a

/home/wb411133/.conda/envs/geog/lib/python3.9/site-packages/shapely/topology.py:19: ShapelyDeprecationWarning: InvalidGeometryError will derive from ShapelyError and not TypeError or ValueError in Shapely 2.0.
  raise InvalidGeometryError("Null geometry supports no operations")
/home/wb411133/.conda/envs/geog/lib/python3.9/site-packages/shapely/topology.py:19: ShapelyDeprecationWarning: InvalidGeometryError will derive from ShapelyError and not TypeError or ValueError in Shapely 2.0.
  raise InvalidGeometryError("Null geometry supports no operations")
/home/wb411133/.conda/envs/geog/lib/python3.9/site-packages/shapely/topology.py:19: ShapelyDeprecationWarning: InvalidGeometryError will derive from ShapelyError and not TypeError or ValueError in Shapely 2.0.
  raise InvalidGeometryError("Null geometry supports no operations")
/home/wb411133/.conda/envs/geog/lib/python3.9/site-packages/shapely/topology.py:19: ShapelyDeprecationWarning: InvalidGeometryError will derive from ShapelyError a

/home/wb411133/.conda/envs/geog/lib/python3.9/site-packages/shapely/topology.py:19: ShapelyDeprecationWarning: InvalidGeometryError will derive from ShapelyError and not TypeError or ValueError in Shapely 2.0.
  raise InvalidGeometryError("Null geometry supports no operations")
/home/wb411133/.conda/envs/geog/lib/python3.9/site-packages/shapely/topology.py:19: ShapelyDeprecationWarning: InvalidGeometryError will derive from ShapelyError and not TypeError or ValueError in Shapely 2.0.
  raise InvalidGeometryError("Null geometry supports no operations")
/home/wb411133/.conda/envs/geog/lib/python3.9/site-packages/shapely/topology.py:19: ShapelyDeprecationWarning: InvalidGeometryError will derive from ShapelyError and not TypeError or ValueError in Shapely 2.0.
  raise InvalidGeometryError("Null geometry supports no operations")
/home/wb411133/.conda/envs/geog/lib/python3.9/site-packages/shapely/topology.py:19: ShapelyDeprecationWarning: InvalidGeometryError will derive from ShapelyError a

In [92]:
grid.to_file(summary_grid)

In [89]:

# Map the most recently looped grid cell
m = folium.Map(location=[potential_buildings.unary_union.centroid.y, potential_buildings.unary_union.centroid.x], zoom_start=18)
try:
    folium.GeoJson(row['geometry'], 
             style_function=lambda x: {'fillOpacity':0.5, 'fillColor': 'red', 'color':'#520f0a'}).add_to(m)
except:
    pass
try:
    folium.GeoJson(i_par.to_json(), 
               style_function=lambda x: {'fillOpacity':1, 'fillColor': '#6878ed', 'stroke': False}).add_to(m)
except:
    pass
try:
    folium.GeoJson(data=i_bld.to_json(), 
              style_function=lambda x: {'fillOpacity':1,'fillColor': '#ebab15', 'stroke': False}).add_to(m)
except:
    pass
m

# Compare Buildings and Parcels

In [19]:
inB['area'] = inB['geometry'].apply(lambda x: x.area)
inG['area'] = inG['geometry'].apply(lambda x: x.area)

In [24]:
main_size = 50 # size threshold for a building to be considered main

# Summarize buildings in parcels
inP['BLDG_I'] = 0 # buildings intersecting parcel
inP['BLDG_C'] = 0 # buildings contained in parcel
inP['BLDG_M'] = 0 # buildings in parcel > 50m2

inP['BLDG_I_G'] = 0 # same as above, but from Google dataset
inP['BLDG_C_G'] = 0
inP['BLDG_M_G'] = 0
for idx, row in inP.iterrows():    
    # Summarize collected buildings
    potential_buildings = inB.loc[list(b_idx.intersection(row['geometry'].bounds))]
    m_bld = potential_buildings.loc[~potential_buildings.intersects(row['geometry'])]
    i_bld = potential_buildings.loc[potential_buildings.intersects(row['geometry'])]
    c_bld = potential_buildings.loc[potential_buildings['geometry'].apply(lambda x: row['geometry'].contains(x))]    
    inP.loc[idx, 'BLDG_I'] = i_bld.shape[0]
    inP.loc[idx, 'BLDG_C'] = c_bld.shape[0]
    m_bld = i_bld.loc[i_bld['area'] > 50]
    inP.loc[idx, 'BLDG_M'] = m_bld.shape[0]
    
    # Summarize buildings in Google
    potential_buildings = inG.loc[list(g_idx.intersection(row['geometry'].bounds))]
    m_bld_g = potential_buildings.loc[~potential_buildings.intersects(row['geometry'])]
    i_bld_g = potential_buildings.loc[potential_buildings.intersects(row['geometry'])]
    c_bld_g = potential_buildings.loc[potential_buildings['geometry'].apply(lambda x: row['geometry'].contains(x))]    
    inP.loc[idx, 'BLDG_I_G'] = i_bld_g.shape[0]
    inP.loc[idx, 'BLDG_C_G'] = c_bld_g.shape[0]
    m_bld_g = i_bld_g.loc[i_bld_g['area'] > main_size]
    inP.loc[idx, 'BLDG_M_G'] = m_bld_g.shape[0]
    
    '''
    # uncomment this section to stop the loop add a specific index in order to run plotting below
    if idx > 3:
        break
    '''

In [47]:
p_idx = inP.sindex

In [55]:
inB['p_i'] = 0
inB['p_c'] = 0
max_idx = inB.index[-1]
for idx, row in inB.iterrows():
    print(f'{idx} of {max_idx}')
    potential_parcels = inP.loc[list(p_idx.intersection(row['geometry'].bounds))]
    i_par = potential_parcels.loc[potential_parcels.intersects(row['geometry'])]
    c_par = potential_parcels.loc[potential_parcels['geometry'].apply(lambda x: x.contains(row['geometry']))]
    
    inB.loc[idx, 'p_i'] = i_par.shape[0]
    inB.loc[idx, 'p_c'] = c_par.shape[0]

0 of 91385
1 of 91385
2 of 91385
3 of 91385
4 of 91385
5 of 91385
6 of 91385
7 of 91385
8 of 91385
9 of 91385
10 of 91385
11 of 91385
12 of 91385
13 of 91385
14 of 91385
15 of 91385
16 of 91385
17 of 91385
18 of 91385
19 of 91385
20 of 91385
21 of 91385
22 of 91385
23 of 91385
24 of 91385
25 of 91385
26 of 91385
27 of 91385
28 of 91385
29 of 91385
30 of 91385
31 of 91385
32 of 91385
33 of 91385
34 of 91385
35 of 91385
36 of 91385
37 of 91385
38 of 91385
39 of 91385
40 of 91385
41 of 91385
42 of 91385
43 of 91385
44 of 91385
45 of 91385
46 of 91385
47 of 91385
48 of 91385
49 of 91385
50 of 91385
51 of 91385
52 of 91385
53 of 91385
54 of 91385
55 of 91385
56 of 91385
57 of 91385
58 of 91385
59 of 91385
60 of 91385
61 of 91385
62 of 91385
63 of 91385
64 of 91385
65 of 91385
66 of 91385
67 of 91385
68 of 91385
69 of 91385
70 of 91385
71 of 91385
72 of 91385
73 of 91385
74 of 91385
75 of 91385
76 of 91385
77 of 91385
78 of 91385
79 of 91385
80 of 91385
81 of 91385
82 of 91385
83 of 91385
84

668 of 91385
669 of 91385
670 of 91385
671 of 91385
672 of 91385
673 of 91385
674 of 91385
675 of 91385
676 of 91385
677 of 91385
678 of 91385
679 of 91385
680 of 91385
681 of 91385
682 of 91385
683 of 91385
684 of 91385
685 of 91385
686 of 91385
687 of 91385
688 of 91385
689 of 91385
690 of 91385
691 of 91385
692 of 91385
693 of 91385
694 of 91385
695 of 91385
696 of 91385
697 of 91385
698 of 91385
699 of 91385
700 of 91385
701 of 91385
702 of 91385
703 of 91385
704 of 91385
705 of 91385
706 of 91385
707 of 91385
708 of 91385
709 of 91385
710 of 91385
711 of 91385
712 of 91385
713 of 91385
714 of 91385
715 of 91385
716 of 91385
717 of 91385
718 of 91385
719 of 91385
720 of 91385
721 of 91385
722 of 91385
723 of 91385
724 of 91385
725 of 91385
726 of 91385
727 of 91385
728 of 91385
729 of 91385
730 of 91385
731 of 91385
732 of 91385
733 of 91385
734 of 91385
735 of 91385
736 of 91385
737 of 91385
738 of 91385
739 of 91385
740 of 91385
741 of 91385
742 of 91385
743 of 91385
744 of 91385

1295 of 91385
1296 of 91385
1297 of 91385
1298 of 91385
1299 of 91385
1300 of 91385
1301 of 91385
1302 of 91385
1303 of 91385
1304 of 91385
1305 of 91385
1306 of 91385
1307 of 91385
1308 of 91385
1309 of 91385
1310 of 91385
1311 of 91385
1312 of 91385
1313 of 91385
1314 of 91385
1315 of 91385
1316 of 91385
1317 of 91385
1318 of 91385
1319 of 91385
1320 of 91385
1321 of 91385
1322 of 91385
1323 of 91385
1324 of 91385
1325 of 91385
1326 of 91385
1327 of 91385
1328 of 91385
1329 of 91385
1330 of 91385
1331 of 91385
1332 of 91385
1333 of 91385
1334 of 91385
1335 of 91385
1336 of 91385
1337 of 91385
1338 of 91385
1339 of 91385
1340 of 91385
1341 of 91385
1342 of 91385
1343 of 91385
1344 of 91385
1345 of 91385
1346 of 91385
1347 of 91385
1348 of 91385
1349 of 91385
1350 of 91385
1351 of 91385
1352 of 91385
1353 of 91385
1354 of 91385
1355 of 91385
1356 of 91385
1357 of 91385
1358 of 91385
1359 of 91385
1360 of 91385
1361 of 91385
1362 of 91385
1363 of 91385
1364 of 91385
1365 of 91385
1366 o

1928 of 91385
1929 of 91385
1930 of 91385
1931 of 91385
1932 of 91385
1933 of 91385
1934 of 91385
1935 of 91385
1936 of 91385
1937 of 91385
1938 of 91385
1939 of 91385
1940 of 91385
1941 of 91385
1942 of 91385
1943 of 91385
1944 of 91385
1945 of 91385
1946 of 91385
1947 of 91385
1948 of 91385
1949 of 91385
1950 of 91385
1951 of 91385
1952 of 91385
1953 of 91385
1954 of 91385
1955 of 91385
1956 of 91385
1957 of 91385
1958 of 91385
1959 of 91385
1960 of 91385
1961 of 91385
1962 of 91385
1963 of 91385
1964 of 91385
1965 of 91385
1966 of 91385
1967 of 91385
1968 of 91385
1969 of 91385
1970 of 91385
1971 of 91385
1972 of 91385
1973 of 91385
1974 of 91385
1975 of 91385
1976 of 91385
1977 of 91385
1978 of 91385
1979 of 91385
1980 of 91385
1981 of 91385
1982 of 91385
1983 of 91385
1984 of 91385
1985 of 91385
1986 of 91385
1987 of 91385
1988 of 91385
1989 of 91385
1990 of 91385
1991 of 91385
1992 of 91385
1993 of 91385
1994 of 91385
1995 of 91385
1996 of 91385
1997 of 91385
1998 of 91385
1999 o

2561 of 91385
2562 of 91385
2563 of 91385
2564 of 91385
2565 of 91385
2566 of 91385
2567 of 91385
2568 of 91385
2569 of 91385
2570 of 91385
2571 of 91385
2572 of 91385
2573 of 91385
2574 of 91385
2575 of 91385
2576 of 91385
2577 of 91385
2578 of 91385
2579 of 91385
2580 of 91385
2581 of 91385
2582 of 91385
2583 of 91385
2584 of 91385
2585 of 91385
2586 of 91385
2587 of 91385
2588 of 91385
2589 of 91385
2590 of 91385
2591 of 91385
2592 of 91385
2593 of 91385
2594 of 91385
2595 of 91385
2596 of 91385
2597 of 91385
2598 of 91385
2599 of 91385
2600 of 91385
2601 of 91385
2602 of 91385
2603 of 91385
2604 of 91385
2605 of 91385
2606 of 91385
2607 of 91385
2608 of 91385
2609 of 91385
2610 of 91385
2611 of 91385
2612 of 91385
2613 of 91385
2614 of 91385
2615 of 91385
2616 of 91385
2617 of 91385
2618 of 91385
2619 of 91385
2620 of 91385
2621 of 91385
2622 of 91385
2623 of 91385
2624 of 91385
2625 of 91385
2626 of 91385
2627 of 91385
2628 of 91385
2629 of 91385
2630 of 91385
2631 of 91385
2632 o

...

89079 of 91385
89080 of 91385
89081 of 91385
89082 of 91385
89083 of 91385
89084 of 91385
89085 of 91385
89086 of 91385
89087 of 91385
89088 of 91385
89089 of 91385
89090 of 91385
89091 of 91385
89092 of 91385
89093 of 91385
89094 of 91385
89095 of 91385
89096 of 91385
89097 of 91385
89098 of 91385
89099 of 91385
89100 of 91385
89101 of 91385
89102 of 91385
89103 of 91385
89104 of 91385
89105 of 91385
89106 of 91385
89107 of 91385
89108 of 91385
89109 of 91385
89110 of 91385
89111 of 91385
89112 of 91385
89113 of 91385
89114 of 91385
89115 of 91385
89116 of 91385
89117 of 91385
89118 of 91385
89119 of 91385
89120 of 91385
89121 of 91385
89122 of 91385
89123 of 91385
89124 of 91385
89125 of 91385
89126 of 91385
89127 of 91385
89128 of 91385
89129 of 91385
89130 of 91385
89131 of 91385
89132 of 91385
89133 of 91385
89134 of 91385
89135 of 91385
89136 of 91385
89137 of 91385
89138 of 91385
89139 of 91385
89140 of 91385
89141 of 91385
89142 of 91385
89143 of 91385
89144 of 91385
89145 of 9

89629 of 91385
89630 of 91385
89631 of 91385
89632 of 91385
89633 of 91385
89634 of 91385
89635 of 91385
89636 of 91385
89637 of 91385
89638 of 91385
89639 of 91385
89640 of 91385
89641 of 91385
89642 of 91385
89643 of 91385
89644 of 91385
89645 of 91385
89646 of 91385
89647 of 91385
89648 of 91385
89649 of 91385
89650 of 91385
89651 of 91385
89652 of 91385
89653 of 91385
89654 of 91385
89655 of 91385
89656 of 91385
89657 of 91385
89658 of 91385
89659 of 91385
89660 of 91385
89661 of 91385
89662 of 91385
89663 of 91385
89664 of 91385
89665 of 91385
89666 of 91385
89667 of 91385
89668 of 91385
89669 of 91385
89670 of 91385
89671 of 91385
89672 of 91385
89673 of 91385
89674 of 91385
89675 of 91385
89676 of 91385
89677 of 91385
89678 of 91385
89679 of 91385
89680 of 91385
89681 of 91385
89682 of 91385
89683 of 91385
89684 of 91385
89685 of 91385
89686 of 91385
89687 of 91385
89688 of 91385
89689 of 91385
89690 of 91385
89691 of 91385
89692 of 91385
89693 of 91385
89694 of 91385
89695 of 9

90182 of 91385
90183 of 91385
90184 of 91385
90185 of 91385
90186 of 91385
90187 of 91385
90188 of 91385
90189 of 91385
90190 of 91385
90191 of 91385
90192 of 91385
90193 of 91385
90194 of 91385
90195 of 91385
90196 of 91385
90197 of 91385
90198 of 91385
90199 of 91385
90200 of 91385
90201 of 91385
90202 of 91385
90203 of 91385
90204 of 91385
90205 of 91385
90206 of 91385
90207 of 91385
90208 of 91385
90209 of 91385
90210 of 91385
90211 of 91385
90212 of 91385
90213 of 91385
90214 of 91385
90215 of 91385
90216 of 91385
90217 of 91385
90218 of 91385
90219 of 91385
90220 of 91385
90221 of 91385
90222 of 91385
90223 of 91385
90224 of 91385
90225 of 91385
90226 of 91385
90227 of 91385
90228 of 91385
90229 of 91385
90230 of 91385
90231 of 91385
90232 of 91385
90233 of 91385
90234 of 91385
90235 of 91385
90236 of 91385
90237 of 91385
90238 of 91385
90239 of 91385
90240 of 91385
90241 of 91385
90242 of 91385
90243 of 91385
90244 of 91385
90245 of 91385
90246 of 91385
90247 of 91385
90248 of 9

90761 of 91385
90762 of 91385
90763 of 91385
90764 of 91385
90765 of 91385
90766 of 91385
90767 of 91385
90768 of 91385
90769 of 91385
90770 of 91385
90771 of 91385
90772 of 91385
90773 of 91385
90774 of 91385
90775 of 91385
90776 of 91385
90777 of 91385
90778 of 91385
90779 of 91385
90780 of 91385
90781 of 91385
90782 of 91385
90783 of 91385
90784 of 91385
90785 of 91385
90786 of 91385
90787 of 91385
90788 of 91385
90789 of 91385
90790 of 91385
90791 of 91385
90792 of 91385
90793 of 91385
90794 of 91385
90795 of 91385
90796 of 91385
90797 of 91385
90798 of 91385
90799 of 91385
90800 of 91385
90801 of 91385
90802 of 91385
90803 of 91385
90804 of 91385
90805 of 91385
90806 of 91385
90807 of 91385
90808 of 91385
90809 of 91385
90810 of 91385
90811 of 91385
90812 of 91385
90813 of 91385
90814 of 91385
90815 of 91385
90816 of 91385
90817 of 91385
90818 of 91385
90819 of 91385
90820 of 91385
90821 of 91385
90822 of 91385
90823 of 91385
90824 of 91385
90825 of 91385
90826 of 91385
90827 of 9

91322 of 91385
91323 of 91385
91324 of 91385
91325 of 91385
91326 of 91385
91327 of 91385
91328 of 91385
91329 of 91385
91330 of 91385
91331 of 91385
91332 of 91385
91333 of 91385
91334 of 91385
91335 of 91385
91336 of 91385
91337 of 91385
91338 of 91385
91339 of 91385
91340 of 91385
91341 of 91385
91342 of 91385
91343 of 91385
91344 of 91385
91345 of 91385
91346 of 91385
91347 of 91385
91348 of 91385
91349 of 91385
91350 of 91385
91351 of 91385
91352 of 91385
91353 of 91385
91354 of 91385
91355 of 91385
91356 of 91385
91357 of 91385
91358 of 91385
91359 of 91385
91360 of 91385
91361 of 91385
91362 of 91385
91363 of 91385
91364 of 91385
91365 of 91385
91366 of 91385
91367 of 91385
91368 of 91385
91369 of 91385
91370 of 91385
91371 of 91385
91372 of 91385
91373 of 91385
91374 of 91385
91375 of 91385
91376 of 91385
91377 of 91385
91378 of 91385
91379 of 91385
91380 of 91385
91381 of 91385
91382 of 91385
91383 of 91385
91384 of 91385
91385 of 91385


In [56]:
contained_buildings = (inB['p_c'] > 0).sum()
intersecting_buildings = (inB['p_i'] > 0).sum()

In [60]:
print(f'Total buildings: {inB.shape[0]}')
print(f'Floating buildings: {inB.shape[0] - intersecting_buildings}')
print(f'Buildings with >1 parcel: {(inB["p_i"] > 1).sum()}')
print(f'Buildings crossing bounds: {intersecting_buildings - contained_buildings}')

Total buildings: 91386
Floating buildings: 1647
Buildings with >1 parcel: 11859
Buildings crossing bounds: 28466


In [27]:
# Parcels with more than one 'Main' building
inP.loc[inP['BLDG_M'] > 1].shape

(21884, 11)

In [41]:
contained_buildings = inP['BLDG_C'].sum()

In [43]:
# Summarize building stats
print(f'Total Buildings: {inB.shape[0]}')
print(f"Main Buildings: {inB.loc[inB['area'] > 50].shape[0]}")
print(f'Contained Buildings: {contained_buildings}')    

Total Buildings: 91386
Main Buildings: 85654
Contained Buildings: 61883


In [33]:
allP = inP

OWNER_OCCU  WARD             LGA  STATE BLD_HGT_MT  \
0   MR PETER IBOBO NNAEMEKA  OKWE  OSHIMILI SOUTH  DELTA        3.5   
1           MR HENRY IWEBOR  OKWE  OSHIMILI SOUTH  DELTA          7   
2           MR HENRY IWEBOR  OKWE  OSHIMILI SOUTH  DELTA          7   
3   MR. ONYINYE E. ORABUCHI  OKWE  OSHIMILI SOUTH  DELTA        3.5   
4  MR. ALOYSIUS .C. NWAORIE  OKWE  OSHIMILI SOUTH  DELTA        3.5   

       BLD_USE     WALL_MATRL ROOF_MATRL GRID_CONCT CITY_TOWN  \
0  RESIDENTIAL  BRICKS/BLOCKS  ALUMINIUM  CONNECTED     ASABA   
1  RESIDENTIAL  BRICKS/BLOCKS  ALUMINIUM  CONNECTED     ASABA   
2  RESIDENTIAL  BRICKS/BLOCKS  ALUMINIUM  CONNECTED     ASABA   
3  RESIDENTIAL  BRICKS/BLOCKS  ALUMINIUM  CONNECTED     ASABA   
4  RESIDENTIAL  BRICKS/BLOCKS  ALUMINIUM  CONNECTED     ASABA   

                                            STR_NAME  BLD_SIZE_M  CENTROIDX  \
0  ALONG ODUKE ROAD, ODUKE OKWE OSHIMILI SOUTH LO...  351.500125   6.734611   
1  BEHIND ODUKE POLICE POST OKWE OSHIMILI SOUTH L...  264.000947   6.734004   
2  BEHIND ODUKE POLICE POST OKWE OSHIMILI SOUTH L...  314.498744   6.734149   
3  AT OKWE OSHIMILI SOUTH LOCAL GOVT AREA DELTA S...  197.999420   6.734765   
4  AT OKWE ASABA OSHIMILI SOUTH LOCAL GOVERNMENT ...   38.999242   6.734805   

   CENTROIDY                                           geometry        area  
0   6.162495  POLYGON ((749683.919 687343.686, 749697.086 68...  357.668821  
1   6.160677  POLYGON ((749620.176 687140.517, 749631.551 68...  268.632022  
2   6.160688  POLYGON ((749635.547 687142.968, 749647.624 68...  320.015723  
3   6.160669  POLYGON ((749718.327 687121.353, 749702.687 68...  201.472909  
4   6.160533  POLYGON ((749717.083 687107.884, 749712.820 68...   39.683385

In [34]:
inB.sort_values('area')

OWNER_OCCU  \
86907             MR.  & MRS.  CHRISTOPHER  A. AKPUOYE   
91313              DELTA STATE POLYTECHNIC OGWASHI UKU   
90475                             ADMIRALTY UNIVERSITY   
80513                                 MR MORBA HYCINTA   
90035  THE REDEEMED CHRISTIAN CHURCH OF GOD EKREDJEBOR   
...                                                ...   
71227                         LIFE FLOUR MILL NIGERIA   
71220                         LIFE FLOUR MILL NIGERIA   
71354                 SAPELE PHCN POWER STATION (NIPP)   
66476                                            A.T.P   
76614                            STEPHEN KESHI STADIUM   

                          WARD             LGA  STATE BLD_HGT_MT  \
86907       UMUEZEAGWU/OKPONTA  OSHIMILI NORTH  DELTA        3.5   
91313                    OTULU   ANIOCHA SOUTH  DELTA        3.5   
90475                    OTULU   ANIOCHA SOUTH  DELTA        3.5   
80513           OKPANAM/UGBOLU  OSHIMILI NORTH  DELTA        3.5   
90035  AFIESERE/EREUMUKOHWAREN   UGHELLI NORTH  DELTA        3.5   
...                        ...             ...    ...        ...   
71227                 AMUOGODO          SAPELE  DELTA        3.5   
71220                 AMUOGODO          SAPELE  DELTA        3.5   
71354                 AMUOGODO          SAPELE  DELTA       10.5   
66476                 AYOMANOR          SAPELE  DELTA        3.5   
76614                UGBOMANTA  OSHIMILI SOUTH  DELTA        3.5   

                       BLD_USE     WALL_MATRL      ROOF_MATRL GRID_CONCT  \
86907              RESIDENTIAL  BRICKS/BLOCKS       ALUMINIUM  CONNECTED   
91313  EDUCATIONAL INSTITUTION         BLOCKS        ASBESTOS  CONNECTED   
90475  EDUCATIONAL INSTITUTION         BLOCKS        ASBESTOS  CONNECTED   
80513               COMMERCIAL  BRICKS/BLOCKS       ALUMINIUM  CONNECTED   
90035    RELIGIOUS INSTITUTION         BLOCKS        ASBESTOS  CONNECTED   
...                        ...            ...             ...        ...   
71227               INDUSTRIAL  BRICKS/BLOCKS        ASBESTOS  CONNECTED   
71220               INDUSTRIAL  BRICKS/BLOCKS        ASBESTOS  CONNECTED   
71354                  UTILITY          STEEL  TENT/TURPOLINE  CONNECTED   
66476               INDUSTRIAL  BRICKS/BLOCKS       ALUMINIUM  CONNECTED   
76614             RECREATIONAL  BRICKS/BLOCKS       ALUMINIUM  CONNECTED   

           CITY_TOWN                                           STR_NAME  \
86907          IBUSA  AT ETUOKWU FAMILY LAND ALONG OKPONTA ROAD OKPO...   
91313          ASABA                                               None   
90475          ASABA                                               None   
80513          ASABA                                               None   
90035          WARRI                                               None   
...              ...                                                ...   
71227  SAPELE/AMUKPE                                    SAPELE, NIGERIA   
71220  SAPELE/AMUKPE                                    SAPELE, NIGERIA   
71354  SAPELE/AMUKPE                       14 OGODO RD, SAPELE, NIGERIA   
66476  SAPELE/AMUKPE                 SAPELE-WARRI ROAD, SAPELE, NIGERIA   
76614          ASABA                                       NNEBISI ROAD   

         BLD_SIZE_M  CENTROIDX  CENTROIDY  \
86907      2.499910   6.621691   6.166378   
91313      2.500290   6.563120   6.221177   
90475      3.000222   6.575916   6.164971   
80513      4.000394   6.662643   6.218856   
90035      4.375090   6.026202   5.511741   
...             ...        ...        ...   
71227   9169.856072   5.658533   5.915672   
71220   9449.881880   5.655526   5.917748   
71354  13247.750189   5.645181   5.925343   
66476  14998.263769   5.693828   5.893174   
76614  26744.748938   6.722431   6.206579   

                                                geometry          area  
86907  POLYGON ((737123.125 687768.144, 737124.425 68...      2.543415  
91313  POLYGON ((730603.428 6